#### Light GBM, XGBoostun egitim suresi performansini artirmaya yonelik gelistirilen bir diger GBM turudur

In [3]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.preprocessing import scale, StandardScaler
from sklearn.metrics import mean_squared_error, r2_score

from sklearn.linear_model import LinearRegression
from sklearn.tree import DecisionTreeRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.svm import SVR


from warnings import filterwarnings
filterwarnings('ignore')

In [4]:
df = pd.read_csv('Hitters.csv')
df = df.dropna()
dms= pd.get_dummies(df[['League','Division','NewLeague']]) #kategorik degiskenleri dummy degiskenlere donusturduk
y=df["Salary"]
X_ = df.drop(['Salary','League','Division','NewLeague'],axis=1).astype('float64')# bu 4 sutun kaldirir kalan sutunlari da float64 veri turune cevirir
X=pd.concat([X_,dms[['League_N','Division_W','NewLeague_N']]],axis=1)
X_train,X_test,y_train,y_test = train_test_split(X,y,test_size=0.25,random_state=42)

In [7]:
!pip install lightgbm

In [9]:
from lightgbm import LGBMRegressor

In [11]:
lgb_model = LGBMRegressor().fit(X_train,y_train)

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000452 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 831
[LightGBM] [Info] Number of data points in the train set: 197, number of used features: 19
[LightGBM] [Info] Start training from score 543.483442
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: 

In [15]:
lgb_model 

LGBMRegressor()

In [17]:
y_pred = lgb_model.predict(X_test)

In [19]:
np.sqrt(mean_squared_error(y_test,y_pred))

363.8712087611089

In [21]:
lgbm_params = {
    "learning_rate": [0.01, 0.05, 0.1],
    "n_estimators": [100, 200, 300],
    "max_depth": [-1], # -1 genellikle num_leaves tarafından kontrol edilmesini sağlar, ya da [3, 4, 5] gibi küçük bir aralık
    "num_leaves": [10, 15, 20, 25], # max_depth'ten daha önemli olabilir
    "min_child_samples": [10, 15, 20], # Veri setiniz küçük olduğu için önemli
    # "lambda_l1": [0, 0.01, 0.1],
    # "lambda_l2": [0, 0.01, 0.1],
    # "feature_fraction": [0.8, 0.9, 1.0],
    # "bagging_fraction": [0.8, 0.9, 1.0],
    # "bagging_freq": [1, 3] # bagging_fraction < 1.0 ise kullanılır
}

In [ ]:
lgbm_cv_model = GridSearchCV(lgb_model , lgbm_params , cv = 10 , n_jobs = -1 , verbose = 2).fit(X_train,y_train)

Fitting 10 folds for each of 108 candidates, totalling 1080 fits
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002466 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 766
[LightGBM] [Info] Number of data points in the train set: 177, number of used features: 19
[LightGBM] [Info] Start training from score 556.882701
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001527 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 762
[LightGBM] [Info] Number of data points in the train set: 177, number of used features: 19
[LightGBM] [Info] Start training from score 526.474040
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000954 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bin

In [26]:
lgbm_cv_model.best_params_

{'learning_rate': 0.01,
 'max_depth': -1,
 'min_child_samples': 15,
 'n_estimators': 200,
 'num_leaves': 15}

In [30]:
lgbm_tuned = LGBMRegressor ( learning_rate = 0.01 , max_depth =-1 , min_child_samples = 15 , n_estimators = 200 , num_leaves = 15).fit(X_train,y_train)

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000294 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 831
[LightGBM] [Info] Number of data points in the train set: 197, number of used features: 19
[LightGBM] [Info] Start training from score 543.483442
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

In [32]:
y_pred = lgbm_tuned.predict(X_test)

In [34]:
np.sqrt(mean_squared_error(y_test,y_pred))

370.4269665811574